In [1]:
import pandas as pd
from html import unescape
import re
import numpy as np
from collections import Counter

import nltk
from nltk import tokenize as tknz
from nltk.corpus import stopwords

from nltk.stem import PorterStemmer, WordNetLemmatizer
from nltk.corpus import wordnet
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
import gensim

import spacy
from spacy import displacy
import en_core_web_md

import pickle

c:\program files\python38\lib\site-packages\spacy\util.py:275: UserWarning: [W031] Model 'en_core_web_md' (2.2.0) requires spaCy v2.2 and is incompatible with the current spaCy version (2.3.5). This may lead to unexpected results or runtime errors. To resolve this, download a newer compatible model or retrain your custom model with the current spaCy version. For more details and available updates, run: python -m spacy validate
  warnings.warn(warn_msg)


In [2]:
with open('data.pickle', 'rb') as f:
    data = pickle.load(f)

In [3]:
data['clean_tweet']

0        when father is dysfunctional and is so selfish...
1        thanks for lyft credit cannot use cause they d...
2                                      bihday your majesty
3        model love yoyou take with yoyou all the time ...
4                        factsguide society now motivation
                               ...                        
49154    thought factory leftright polarisation trump u...
49155    feeling like mermaid hairflip neverready forma...
49156    hillary campaigned today in ohioomg amp used w...
49157    happy at work conference right mindset leads t...
49158    my song so glad free download shoegaze newmusi...
Name: clean_tweet, Length: 49159, dtype: object

**Задание 1.**

Используя библиотеку `Spacy`, вывести ТОП-20 популярных NER в `combine_df` датасете. Какой тип NER (ORG, GPE, PERSON и тд) оказался самым популярным? (Учтите, что `max_word_limit_spacy` для Spacy = 1000000)

In [4]:
corpus = [''.join(i) for i in data['clean_tweet']]
corpus = '. '.join(corpus)
corpus = corpus[0:1000000]

In [5]:
corpus

'when father is dysfunctional and is so selfish he drags his kids into his dysfunction run. thanks for lyft credit cannot use cause they do not offer wheelchair vans in pdx disapointed getthanked. bihday your majesty. model love yoyou take with yoyou all the time in yoyour. factsguide society now motivation. huge fan fare and big talking before they leave chaos and pay disputes when they get there allshowandnogo. camping tomorrow danny. the next school year is the year for exams cannot think about that school exams hate imagine actorslife revolutionschool girl. we won love the land allin cavs champions cleveland clevelandcavaliers. welcome here am it has it is so gr. ireland consumer price index mom climbed from previous to in may blog silver gold forex. we are so selfish orlando standwithorlando pulseshooting orlandoshooting biggerproblems selfish heabreaking values love. get to see my daddy today days gettingfed. cnn calls michigan middle school build the wall chant tcot. no comment 

In [6]:
nlp = en_core_web_md.load()
article = nlp(corpus)
displacy.render(article, jupyter=True, style='ent')

In [7]:
ents = [ent.label_ for ent in article.ents]

In [8]:
Counter(ents).keys() # equals to list(set(words))

dict_keys(['GPE', 'ORG', 'DATE', 'PERSON', 'NORP', 'TIME', 'ORDINAL', 'PRODUCT', 'CARDINAL', 'FAC', 'LOC', 'LAW', 'EVENT', 'WORK_OF_ART', 'MONEY', 'QUANTITY', 'LANGUAGE'])

In [9]:
Counter(ents).values() # counts the elements' frequency

dict_values([1713, 1189, 2766, 2285, 494, 596, 200, 112, 320, 137, 117, 5, 60, 42, 3, 2, 9])

*самые популярные категории `DATE` и `PERSON`*

С помощью Spacy выяснить: какие персоны и организации самые обсуждаемые в train и test датасетах? вывести ТОП-20 самых популярных. Действительно ли в топ вошли только персоны и организации или есть мусор?

In [10]:
items = [x.text for x in article.ents if (x.label_=='ORG' or x.label_=='PERSON')] 
Counter(items).most_common(20)

[('obama', 33),
 ('bing bong bing bong', 31),
 ('gop', 20),
 ('nba', 18),
 ('hillary', 18),
 ('hu', 17),
 ('orlando', 17),
 ('netflix', 15),
 ('islam', 15),
 ('lebron', 13),
 ('nyc', 11),
 ('god', 11),
 ('christina grimmie', 10),
 ('fed', 10),
 ('stas', 10),
 ('aww', 9),
 ('disney', 9),
 ('allahsoil', 9),
 ('blm', 9),
 ('eu', 9)]

*встречается мусор*

**Задание 2.**

Используя библиотеку `nltk`, вывести ТОП-20 популярных `NER` в `combine_df` датасете. Какой тип NER (ORG, GPE, PERSON и тд) оказался самым популярным? Для данного задания используем ограничение на количество символов во входном датасете (max_word_limit_spacy = 1000000), чтобы иметь возможность сравнить результаты работы `Spacy` и `nltk`. Обратите внимание, что `nltk` чувствителен к регистру.

NLTK дает плохой результат для NER процедуры, т.к. наш датасет полностью в нижнем регистре.

In [14]:
corpus = corpus.title()

In [16]:
ne_tree = nltk.ne_chunk(nltk.pos_tag(nltk.word_tokenize(corpus)))

In [19]:
{(' '.join(c[0] for c in chunk), chunk.label() ) for chunk in ne_tree if hasattr(chunk, 'label') }

{('Animals Walrus Animals Animation', 'PERSON'),
 ('Oyout Iphone', 'PERSON'),
 ('Angry Reaction', 'ORGANIZATION'),
 ('Blog Health Essentialoils', 'ORGANIZATION'),
 ('Dress Wedding Stuff Via Momlife Family Wedding Mommylife Fa', 'PERSON'),
 ('Spit', 'PERSON'),
 ('Of First Nations Vi', 'ORGANIZATION'),
 ('Endof Tedtalks Tedatibm', 'PERSON'),
 ('Us Too Stanleycup', 'PERSON'),
 ('Banner Merry Christmas', 'PERSON'),
 ('Shikaarei Songtell', 'ORGANIZATION'),
 ('Pathfinder Meets', 'ORGANIZATION'),
 ('Angry Person Via Goes', 'PERSON'),
 ('Fire And Then Made Rule', 'ORGANIZATION'),
 ('Network Has Gone Again', 'ORGANIZATION'),
 ('Bigot', 'PERSON'),
 ('Albanpilgrimage', 'ORGANIZATION'),
 ('Ceain People Sorry Notnamingnames Feelingignored Justwannatalk', 'PERSON'),
 ('School Ready', 'PERSON'),
 ('Herself', 'PERSON'),
 ('Bottom Of My Hea', 'ORGANIZATION'),
 ('Hard Work Toby Has Had An Awesome', 'PERSON'),
 ('Cena De Cumple Thanks Mom', 'PERSON'),
 ('Wti Drops', 'PERSON'),
 ('Bench', 'GPE'),
 ('Sweet

Как видим, приведение каждого слова к верхнему регистру провоцирует алгоритм на некорректную классифкацию почти каждого из слов в состав `ORGANIZATION` или `PERSON`

**Задание 3.**

Какая из библиотек по вашему лучше отработала? Сравните качество полученных most_common NER и количество распознаных NER.

`Spacy` более подходящая библиотека в данном случае, т.к. отсутсвует зависимость от регистра